<a href="https://colab.research.google.com/github/shivanandiyer/ANLP_G33/blob/main/pymed_extraction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Install pymed and Berttopic

https://pypi.org/project/pymed/
https://maartengr.github.io/BERTopic/index.html


In [1]:
!pip install pymed

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [2]:
!pip install bertopic

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 120.7/120.7 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 52.9 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 kB 295.2 kB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 10.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 73.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 51.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 22.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 52.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   

# Search and retrieve Pubmed Data to a dataframe via Pymed API

## Extract all articles starting May 2018

In [8]:
from pymed import PubMed
import pandas as pd
pubmed = PubMed(tool="PubMedSearcher", email="shivanand.iyer@gmail.com")

############################################################################################
## PUT YOUR SEARCH TERM HERE ##
#search_term = "Cardiovascular Diseases"
search_term = '(("2018/05/01"[Date - Create] : "2025"[Date - Create])) AND (Cardiovascular Diseases)'

## PUT YOUR SEARCH TERM HERE ##
############################################################################################

results = pubmed.query(search_term, max_results=5000)
articleList = []
articleInfo = []

for article in results:
# Print the type of object we've found (can be either PubMedBookArticle or PubMedArticle).
# We need to convert it to dictionary with available function
    articleDict = article.toDict()
    articleList.append(articleDict)

# Generate list of dict records which will hold all article details that could be fetch from PUBMED API
for article in articleList:


#Sometimes article['pubmed_id'] contains list separated with comma - take first pubmedId in that list - thats article pubmedId
    pubmedId = article['pubmed_id'].partition('\n')[0]
    # Append article info to dictionary 
    #articleInfo.append({u'pubmed_id':pubmedId,
    #                   u'title':article['title'],
    #                   u'keywords':article['keywords'],
    #                   u'journal':article['journal'],
    #                   u'abstract':article['abstract'],
    #                   u'conclusions':article['conclusions'],
    #                   u'methods':article['methods'],
    #                   u'results': article['results'],
    #                   u'copyrights':article['copyrights'],
    #                   u'doi':article['doi'],
    #                   u'publication_date':article['publication_date'], 
    #                   u'authors':article['authors']})
    articleInfo.append({u'pubmed_id':pubmedId,
                       u'title':article['title'],
                       u'abstract':article['abstract'],
                       u'authors':article['authors'],
                       u'publication_date':article['publication_date']})
articlesPD = pd.DataFrame.from_dict(articleInfo)
articlesPD=articlesPD.dropna()
export_csv = articlesPD.to_csv ('cardiovascular_diseases.csv', index = None, header=True) 
#Print first 10 rows of dataframe
articlesPD.head(10)

pubmed_id                                              title  \
0  37165382  Study design and protocol of a stepped wedge c...   
1  37165317  Campylobacter prevalence from food, animals, h...   
2  37165232  Alcohol and the vasculature: a love-hate relat...   
3  37165203  Incomplete penetrance and variable expressivit...   
4  37165163  MicroRNA regulation of phenotypic transformati...   
5  37165157  The contribution of the exposome to the burden...   
6  37164973  Roles of obesity in mediating the causal effec...   
7  37164887  Contribution of low skeletal muscle mass in pr...   
8  37164882  Ultrasound for diagnosis of interstitial lung ...   
9  37164689  Relationship between Saturated Fatty Acid Inta...   

                                            abstract publication_date  
0  As people living with HIV (PLWH) experience ea...       2023-05-11  
1  Campylobacter regarded as a major cause of foo...       2023-05-11  
2  Alcohol consumption is a leading risk factor a...       2023-05-11  
3  Monogenic Forms of Diabetes (MFD) account for ...       2023-05-11  
4  Alterations in the vascular smooth muscle cell...       2023-05-11  
5  Large epidemiological and health impact assess...       2023-05-11  
6  Previous observational studies have reported p...       2023-05-11  
7  We aimed to explore the association between sk...       2023-05-11  
8  Patients with diffuse connective tissue diseas...       2023-05-11  
9  Hypertension is one of the most prevalent dise...       2023-05-11

## Append Publication Year from the Date

In [9]:
articlesPD['publication_year'] = pd.to_datetime(articlesPD['publication_date']).dt.strftime('%Y')

## Convert Article Abstracts to a list for Topic Modelling

In [10]:
docs=articlesPD["abstract"].tolist()

## Training

We start by instantiating BERTopic. We set language to `english` since our documents are in the English language. 

Calculate the topic probabilities. However, this can slow down BERTopic significantly at large amounts of data (>100_000 documents). It is advised to turn this off if you want to speed up the model. 


In [11]:
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

vectorizer_model = CountVectorizer(stop_words="english")

topic_model = BERTopic(language="english", calculate_probabilities=False, verbose=True,vectorizer_model=vectorizer_model)
topics, probs = topic_model.fit_transform(docs)

Batches:   0%|          | 0/139 [00:00<?, ?it/s]

2023-05-11 05:03:13,412 - BERTopic - Transformed documents to Embeddings
2023-05-11 05:03:50,604 - BERTopic - Reduced dimensionality
2023-05-11 05:03:50,832 - BERTopic - Clustered reduced embeddings


In [ ]:
topics_per_class = topic_model.topics_per_class(docs, classes=classes)

# Extracting Topics
After fitting the model, we look at the results- the most frequent topics first as they best represent the collection of documents

In [13]:
freq = topic_model.get_topic_info(); freq.head(5)

Topic  Count                                      Name
0     -1   1241  -1_patients_cardiovascular_study_disease
1      0    185         0_af_atrial_bleeding_fibrillation
2      1    140      1_cholesterol_lipoprotein_statin_lpa
3      2    116      2_covid19_sarscov2_infection_vaccine
4      3    114                          3_ca_nil_global_

## Select the most frequent topic

In [14]:
topic_model.get_topic(0)  

[('af', 0.03038377828554995),
 ('atrial', 0.02389002586426501),
 ('bleeding', 0.020122824256702202),
 ('fibrillation', 0.01874510061304824),
 ('anticoagulation', 0.017538069804688302),
 ('vte', 0.01737114765941463),
 ('patients', 0.016222604488313346),
 ('pe', 0.013838805513056149),
 ('risk', 0.01141426142769926),
 ('oral', 0.011024121197294663)]

In [15]:
topic_model.get_document_info(docs)

Document  Topic  \
0     As people living with HIV (PLWH) experience ea...     48   
1     Campylobacter regarded as a major cause of foo...     -1   
2     Alcohol consumption is a leading risk factor a...     -1   
3     Monogenic Forms of Diabetes (MFD) account for ...     -1   
4     Alterations in the vascular smooth muscle cell...     18   
...                                                 ...    ...   
4442  Breast cancer survivors live longer due to mor...     26   
4443  Limited data is available on sex differences i...     66   
4444  Heat waves are becoming more intense and extre...     28   
4445  Inherited stress-induced arterial hypertension...     -1   
4446  Insulinomas are rare pancreatic neuroendocrine...     40   

                                          Name  \
0       48_bp_health_hypertension_intervention   
1     -1_patients_cardiovascular_study_disease   
2     -1_patients_cardiovascular_study_disease   
3     -1_patients_cardiovascular_study_disease   
4          18_expression_mirnas_rnas_noncoding   
...                                        ...   
4442     26_depression_anxiety_selfcare_mental   
4443      66_stroke_ischemic_blepharitis_women   
4444              28_air_pollution_pm_exposure   
4445  -1_patients_cardiovascular_study_disease   
4446           40_hemangioma_rare_tumors_tumor   

                                            Top_n_words  Probability  \
0     bp - health - hypertension - intervention - ap...     0.865198   
1     patients - cardiovascular - study - disease - ...     0.000000   
2     patients - cardiovascular - study - disease - ...     0.000000   
3     patients - cardiovascular - study - disease - ...     0.000000   
4     expression - mirnas - rnas - noncoding - lncrn...     0.666465   
...                                                 ...          ...   
4442  depression - anxiety - selfcare - mental - sym...     0.839110   
4443  stroke - ischemic - blepharitis - women - youn...     1.000000   
4444  air - pollution - pm - exposure - climate - pm...     0.123223   
4445  patients - cardiovascular - study - disease - ...     0.000000   
4446  hemangioma - rare - tumors - tumor - benign - ...     0.241916   

      Representative_document  
0                       False  
1                       False  
2                       False  
3                       False  
4                        True  
...                       ...  
4442                    False  
4443                     True  
4444                    False  
4445                    False  
4446                     True  

[4447 rows x 6 columns]

## Visualise Topics

### The Intertopic Distance Map represents the prevalance of the topics and how closely they are related to one another

In [16]:
topic_model.visualize_topics()

## Generate document embeddings and Visualise Documents inside the topics

In [32]:
from sentence_transformers import SentenceTransformer
from umap import UMAP

sentence_model = SentenceTransformer("all-MiniLM-L6-v2")
embeddings = sentence_model.encode(docs, show_progress_bar=True)

# Train BERTopic
topic_model_d = BERTopic().fit(docs, embeddings)

# Run the visualization with the original embeddings
topic_model_d.visualize_documents(docs, embeddings=embeddings)

2023-05-11 06:25:34,890 - BERTopic - Reduced dimensionality
2023-05-11 06:25:35,091 - BERTopic - Clustered reduced embeddings


### Topic Hierarchy

We can see that topics with the same colors have been grouped together. For instance:

Topic 29 (cardiotoxicity, cardiac, myocardial) & 40 (diabetic, cardiac) have been grouped together because of their closeness.

This info is helpful to better understand the reason why the topics have been considered to be similar to one another.

In [17]:
topic_model.visualize_hierarchy(top_n_topics=50)

## Topic Word Scores

Visualize the selected terms for a few topics  and their c-TF-IDF scores for each topic representation. Also comparing the topic representation to each other 

In [18]:
topic_model.visualize_barchart(top_n_topics=10)

## Topic Similarity

Similarity matrix generated by applying cosine similarities through those topic embeddings indicates how similar certain topics are to each other.

In [19]:
topic_model.visualize_heatmap(n_clusters=20, width=1000, height=1000)

In [23]:
# Calculate the topic distributions on a token-level
topic_distr, topic_token_distr = topic_model.approximate_distribution(docs, calculate_tokens=True)

# Visualize the token-level distributions
#df = topic_model.visualize_approximate_distribution(docs[3], topic_token_distr[3])
#df

100%|██████████| 5/5 [00:21<00:00,  4.38s/it]


In [24]:
# Visualize the token-level distributions
df = topic_model.visualize_approximate_distribution(docs[3], topic_token_distr[3])
df

# **Search Topics**

`find_topics` to search for topics that are similar 
to an input search_term. Searching for topics that closely relate the search term. Then, we extract the most similar topic and check the results: 

In [25]:
similar_topics, similarity = topic_model.find_topics("covid", top_n=5); similar_topics

[2, 45, 23, 82, -1]

In [26]:
topic_model.get_topic(50)

[('ace2', 0.041723564599366346),
 ('failure', 0.030242226634720894),
 ('acetazolamide', 0.02997498663624977),
 ('arbs', 0.028160330050466115),
 ('arni', 0.025944106508913618),
 ('ras', 0.025544673841999946),
 ('aceis', 0.02482964575907505),
 ('heart', 0.023513440646101037),
 ('hco3', 0.020587164681159953),
 ('ejection', 0.020501613299482812)]

# Article Summarisation

In [27]:
abs=articlesPD.head(10)
type(abs)

pandas.core.frame.DataFrame

## Summarisation using transfromer library pipeline distilbart summarisation


In [28]:
from transformers import pipeline
summarizer = pipeline("summarization", min_length=50, max_length=150)
abs['summary'] = abs['abstract'].apply(summarizer)

No model was supplied, defaulted to sshleifer/distilbart-cnn-12-6 and revision a4f8f3e (https://huggingface.co/sshleifer/distilbart-cnn-12-6).
Using a pipeline without specifying a model name and revision in production is not recommended.


In [29]:
abs

pubmed_id                                              title  \
0  37165382  Study design and protocol of a stepped wedge c...   
1  37165317  Campylobacter prevalence from food, animals, h...   
2  37165232  Alcohol and the vasculature: a love-hate relat...   
3  37165203  Incomplete penetrance and variable expressivit...   
4  37165163  MicroRNA regulation of phenotypic transformati...   
5  37165157  The contribution of the exposome to the burden...   
6  37164973  Roles of obesity in mediating the causal effec...   
7  37164887  Contribution of low skeletal muscle mass in pr...   
8  37164882  Ultrasound for diagnosis of interstitial lung ...   
9  37164689  Relationship between Saturated Fatty Acid Inta...   

                                            abstract publication_date  \
0  As people living with HIV (PLWH) experience ea...       2023-05-11   
1  Campylobacter regarded as a major cause of foo...       2023-05-11   
2  Alcohol consumption is a leading risk factor a...       2023-05-11   
3  Monogenic Forms of Diabetes (MFD) account for ...       2023-05-11   
4  Alterations in the vascular smooth muscle cell...       2023-05-11   
5  Large epidemiological and health impact assess...       2023-05-11   
6  Previous observational studies have reported p...       2023-05-11   
7  We aimed to explore the association between sk...       2023-05-11   
8  Patients with diffuse connective tissue diseas...       2023-05-11   
9  Hypertension is one of the most prevalent dise...       2023-05-11   

  publication_year                                            summary  
0             2023  [{'summary_text': ' People living with HIV (PL...  
1             2023  [{'summary_text': ' White meat had the highest...  
2             2023  [{'summary_text': ' Alcohol consumption is a l...  
3             2023  [{'summary_text': ' Monogenic Forms of Diabete...  
4             2023  [{'summary_text': ' Alterations in the vascula...  
5             2023  [{'summary_text': ' By 2030, 77% of all deaths...  
6             2023  [{'summary_text': ' ADHD increased the risk of...  
7             2023  [{'summary_text': ' The study included 1365 co...  
8             2023  [{'summary_text': ' Lung ultrasound is a rapid...  
9             2023  [{'summary_text': ' Hypertension is one of the...